In [ ]:
from ipywidgets import interact, interactive, fixed, FloatSlider
from IPython.display import display
import ipywidgets as widgets
import numpy as np
import math
import cvxpy
from inspect import signature
%matplotlib inline

We model the assets in a 1-factor model setting. Namely conditionally on the factor $F$, the assets
are independent, and $r_i$, the return of asset $i$ is given by:
$$r_i = \mu_i + \delta_i(F-\bar F) + \sigma_i \varepsilon_i$$
with $\forall i,\,\textrm{Cov}(F, \varepsilon_i)=0$, and $\varepsilon\sim\mathcal{N}(0, \mathbf{1})$ 

We can show that:
$$\textrm{Corr}(r_i, F)=\rho_i = \frac{\delta_i \sqrt{\textrm{Var}(F)}}{\sqrt{\textrm{Var}(r_i)}}$$
and with $\textrm{Var(r_i)}=\delta_i^2\textrm{Var}(F) + \sigma_i^2$, we get:
$$\rho_i = \frac{1}{\sqrt{1+\frac{\sigma_i^2}{\delta_i^2\textrm{Var(F)}}}}$$
$$\forall i\neq j,\;\textrm{Cov}(r_i, r_j)=\delta_i\delta_j\textrm{Var}(F)$$

In [ ]:
def cor2cov(Rho, vol):
    return np.diag(vol) @ Rho @ np.diag(vol)

def rho(sigma, delta, volF):
    """ computes the correlation between the asset and the factor """
    return 1/math.sqrt(1+sigma**2/(delta**2*volF**2))

def resid_vol(rho, delta, volF):
    """ computes the residual of the asset """
    return math.sqrt(delta**2*volF**2*(1/rho**2-1))

def var(rho, delta, volF):
    """ computes the variance of the asset """
    return delta**2*volF**2+resid_vol(rho, delta, volF)**2

volHY = 0.07
## Edwin's parameters
rho = {'CLO': 0.6,
       'CSO': 0.5,
       'Subprime': 0.3}
delta = {'CLO': 0.4,
         'CSO': 0.2,
         'Subprime': 0.6}
mu = np.array([0.01, 0.075, 0.065, 0.25])

In [ ]:
from matplotlib import pyplot as plt
plt.style.use('ggplot')

In [ ]:
def compute_allocation(rho_clo = 0.9, rho_cso=0.6, rho_subprime=0.2,
             delta_clo=1.2, delta_cso=0.4, delta_subprime=0.8,
             mu_hy=0.02, mu_clo=0.07, mu_cso=0.08, mu_subprime=0.25):
    rho = {'CLO': rho_clo,
           'CSO': rho_cso,
           'Subprime': rho_subprime}
    delta = {'CLO': delta_clo,
             'CSO': delta_cso,
             'Subprime': delta_subprime}
    assets = ['CLO', 'CSO', 'Subprime']
    mu = np.array([mu_hy, mu_clo, mu_cso, mu_subprime])
    u = volHY * np.array([delta[a] for a in assets])
    Sigma = np.outer(u, u) + np.diag([resid_vol(rho[a], delta[a], volHY)**2
                                      for a in assets])
    v = volHY**2 * np.array([1] + [delta[a] for a in assets])
    Sigma = np.vstack((v, np.c_[v[1:], Sigma]))

    sharpe = mu/np.sqrt(np.diag(Sigma))

    gamma = cvxpy.Parameter(sign='positive')
    w = cvxpy.Variable(4)
    ret = mu.T*w
    risk = cvxpy.quad_form(w, Sigma)
    prob = cvxpy.Problem(cvxpy.Maximize(ret-gamma*risk),
                         [cvxpy.sum_entries(w[1:]) - 0.1*w[0] == 1,
                          w[1:] >= 0,
                          w[0] <= 0])

    gamma_x = np.linspace(0, 20, 500)
    W = np.empty((4, gamma_x.size))
    for i, val in enumerate(gamma_x):
        gamma.value = val
        prob.solve()
        W[:,i] = np.asarray(w.value).squeeze()
    fund_return  = mu@W
    fund_vol = np.array([math.sqrt(W[:,i]@Sigma@W[:,i]) for i in range(gamma_x.size)])
    return (W, fund_return, fund_vol)

def plot_allocation(plot_vol=True, **kwargs):
    W, fund_return, fund_vol = compute_allocation(**kwargs)
    gamma_x = np.linspace(0, 20, 500)
    fig, ax1 = plt.subplots()
    ax1.stackplot(gamma_x, W[1:,], labels=['CLO', 'CSO', 'Subprime'])
    ax1.set_xlabel('risk factor')
    ax1.set_ylabel('portfolio weights')
    ax1.legend()
    # ax1.text(0.3, 0.82, 'RMBS')
    # ax1.text(0.5, 0.45, 'CSO')
    # ax1.text(0.5, 0.15, 'CLO')
    ax1.set_ylim([0, 1])
    ax2 = ax1.twinx()
    if plot_vol:
        ax2.plot(gamma_x, fund_vol, lw=1, color="grey")
        ax2.set_ylabel('fund volatility')
    else:
        ax2.plot(gamma_x, fund_return, lw=1, color="grey")
        ax2.set_ylabel('fund return')
    plt.show()


In [ ]:
def desc(greek, asset):
    """returns the latex label"""
    return r'${0}_{{\textrm{{{1}}}}}$'.format('\\'+greek, asset)

desc_mapping = {}
assets = ['CLO', 'CSO', 'Subprime']
for greek in ['rho', 'delta', 'mu']:
    if greek == 'mu':
        assets.append('HY')
    desc_mapping.update({desc(greek, a): '{0}_{1}'.format(greek, a.lower()) for a in assets})
                
w   = interactive(plot_allocation, rho_clo=FloatSlider(description=desc('rho', 'CLO'), min=0., max=1., step=0.1, value=0.9),
          rho_cso=FloatSlider(description=desc('rho', 'CSO'), min=0., max=1., step=0.1, value=0.6),
          rho_subprime=FloatSlider(description=desc('rho', 'Subprime'), min=0., max=1., step=0.1, value=0.2),
          delta_clo=FloatSlider(description=desc('delta', 'CLO'), min=0., max=2., step=0.1, value=1.2),
          delta_cso=FloatSlider(description=desc('delta', 'CSO'), min=0., max=2., step=0.1, value=0.4),
          delta_subprime=FloatSlider(description=desc('delta', 'Subprime'), min=0., max=2., step=0.1, value=0.8),
          mu_hy = FloatSlider(description=desc('mu', 'HY'), min=0., max=.1, step=0.01, value=0.02),
          mu_clo = FloatSlider(description=desc('mu', 'CLO'), min=0., max=.12, step=0.01, value=0.07),
          mu_cso = FloatSlider(description=desc('mu', 'CSO'), min=0., max=.12, step=0.01, value=0.08),
          mu_subprime = FloatSlider(description=desc('mu', 'Subprime'), min=0.1, max=.35, step=0.01, value=0.25))

## black magic to get back to the function order
s = signature(compute_allocation)
param_ordering = {p:i for i, p in enumerate(s.parameters)}
param_ordering[None] = -1
w_ordered = sorted([c for c in w.children], key=lambda x: param_ordering[desc_mapping.get(x.description)])
display(*w_ordered)

In [ ]:
args = w.kwargs.copy()
args.pop('plot_vol')
W, fund_return, fund_vol = compute_allocation(**args)
import pandas as pd
df = pd.DataFrame(np.c_[W.T, fund_return, fund_vol], columns=['HY', 'CLO', 'CSO', 'Subprime', 'return', 'vol'])
df.to_csv('weights.csv', index=False)